In [1]:
import json

In [2]:
import mysql.connector
import json
import pymysql

In [3]:


# Establishing a connection to the MySQL database
conn = mysql.connector.connect(
    host="localhost",
    user="root",
    password="layakishore",
    database ="USERS_DATA")


In [4]:
if conn.is_connected():
    print("Connection to MySQL server is working.")
else:
    print("Connection to MySQL server is not established.")
mycur= conn.cursor()

Connection to MySQL server is working.


In [5]:
database_name = "USERS_DATA"

try:
   # mycur.execute(f"CREATE DATABASE {database_name}")
    print(f"Database '{database_name}' created successfully")
except mysql.connector.Error as err:
    print(f"Error: {err}")

Database 'USERS_DATA' created successfully


In [6]:
create_table_query = """
CREATE TABLE IF NOT EXISTS users4 (
    id VARCHAR(20) PRIMARY KEY,
    name VARCHAR(255),
    screen_name VARCHAR(255),
    location VARCHAR(255),
    verified BOOLEAN,
    followers_count INT,
    statuses_count INT,
    friends_count INT
)
"""

# Execute the query to create the table
#mycur.execute(create_table_query)

In [7]:
mycur.execute("describe Users4")
for X in mycur:
    print(X)

('id', 'varchar(20)', 'NO', 'PRI', None, '')
('name', 'varchar(255)', 'YES', '', None, '')
('screen_name', 'varchar(255)', 'YES', '', None, '')
('location', 'varchar(255)', 'YES', '', None, '')
('verified', 'tinyint(1)', 'YES', '', None, '')
('followers_count', 'int', 'YES', '', None, '')
('statuses_count', 'int', 'YES', '', None, '')
('friends_count', 'int', 'YES', '', None, '')


In [7]:
connection = pymysql.connect(host='localhost',
                             user='root',
                             password='layakishore',
                             database='USERS_DATA',
                             cursorclass=pymysql.cursors.DictCursor)

In [8]:
from elasticsearch import Elasticsearch

# Define Elasticsearch Cloud credentials
cloud_id = "8231a925bb0f402aa30be4fac7ebcd97:dXMtY2VudHJhbDEuZ2NwLmNsb3VkLmVzLmlvOjQ0MyQ1OTg4NzE5MWM5ODc0YjZmODc4ZjA1MmQ2NmI2M2Y1NyQwZmQ2ZWU0YWU4NDQ0NDQ4YjQ1NzI2NmQxMzlmOWI0Mw=="
cloud_auth = ("elastic", "KBDw46EL90pogZZOdcLrmyZ4")  # Credentials for accessing Elasticsearch Cloud

# Create Elasticsearch client with the specified parameters

es = Elasticsearch(cloud_id=cloud_id, basic_auth=cloud_auth)

# Check if the connection is successful
if es.ping():
    print("Connected to Elasticsearch Cloud")
else:
    print("Connection failed")



Connected to Elasticsearch Cloud


In [9]:
index_name = "tweets_final_index"



# Define the mapping
mapping = {
    "settings": {
        "number_of_shards": 9,
        "number_of_replicas": 0,
        "index.mapping.total_fields.limit": 2000
    },
    "mappings": {
        "properties": {
            "created_at": {"type": "date", "format": "EEE MMM dd HH:mm:ss Z yyyy"},
            "id": {"type": "long"},
            "id_str": {"type": "keyword"},
            "text": {"type": "text", "fielddata": True},
            "user": {
                "properties": {
                    "id": {"type": "long"},
                    "id_str": {"type": "keyword"},
                    "name": {"type": "text"},
                    "screen_name": {"type": "keyword"},
                  #  "dynamic": "false"
                }
            },
            "retweeted_status": {
                "properties": {
                    "created_at": {"type": "date", "format": "EEE MMM dd HH:mm:ss Z yyyy"},
                    "id": {"type": "long"},
                    "id_str": {"type": "keyword"},
                    "text": {"type": "text", "fielddata": True},
                    "user": {
                        "properties": {
                            "id": {"type": "long"},
                            "id_str": {"type": "keyword"},
                            "name": {"type": "text"},
                            "screen_name": {"type": "keyword"}
                        }
                    },
                    "retweet_count": {"type": "integer"},
                    "favorite_count": {"type": "integer"},
                    "favorited": {"type": "boolean"},
                    "retweeted": {"type": "boolean"},
                    "possibly_sensitive": {"type": "boolean"}
                }
            },
            "retweet_count": {"type": "integer"},
            "favorite_count": {"type": "integer"},
            "favorited": {"type": "boolean"},
            "retweeted": {"type": "boolean"},
            "possibly_sensitive": {"type": "boolean"}
        }
    }
}

# Create the index with the mapping
if not es.indices.exists(index=index_name):
    es.indices.create(index=index_name, body=mapping, ignore=400)  # ignore 400 already exists code


In [10]:
index_body_tweetids = {
    "settings": {
        "number_of_shards": 5,
        "number_of_replicas": 0,
        "index.mapping.total_fields.limit": 1000,  # Limiting the number of fields
    },
    "mappings": {
        "properties": {
            "tweet_id": {"type": "keyword"},  # Using keyword for exact matches
        }
    }
}

# Create the index
index_name_tweetids = "tweet_ids_final"
if not es.indices.exists(index=index_name_tweetids):
    es.indices.create(index=index_name_tweetids, body=index_body_tweetids)
    print(f"Index '{index_name_tweetids}' created.")
else:
    print(f"Index '{index_name_tweetids}' already exists.")

Index 'tweet_ids_final' already exists.


new index for retweets by this user
new index for likes by this user
new index for recent searches by this user
new index for search?
Relavance Order
Total runtime of the program is 750.3318951129913 seconds

search by string, hashtag,  and user at the minimum. Allow for a time range in these searches. You will also need some notion of relevance to rank the search results. 

Show the meta-data for each tweet such as (a) the author of the tweet,  (b) when it was tweeted, (c) how many times it was retweeted. If the user of the search application clicks on the number of times it was retweeted, show the information about the retweets (who retweeted, when etc.).

If user of the search application clicks on the author, show other tweets by that author or retweets by that author (if available). 

 How you store your information will impact the response times of your query. You must discuss this (in your presentation and report). 

Allow for a time range in these searches?

In [16]:
insert_sql = "INSERT INTO Users4 (id, name, screen_name, location, verified, followers_count, statuses_count, friends_count) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)"

In [17]:
check_sql = "SELECT COUNT(*) FROM Users4 WHERE id = %s"

In [18]:
def preparedTweet(tweet,user_info,retweeted_status,retweeted_user_info,isretweet,engagement_score1=0,engagement_score2=0):
    prepared_tweet = {
                "created_at": tweet.get("created_at"),
                "id": tweet.get("id"),
                "id_str": tweet.get("id_str"),
                "text": tweet.get("text"),
                "user": {
                    "id": user_info.get("id"),
                    "id_str": user_info.get("id_str"),
                    "name": user_info.get("name"),
                    "screen_name": user_info.get("screen_name")
                },
                "isretweet":isretweet,
                "retweeted_status": {
                    "created_at": retweeted_status.get("created_at"),
                    "id": retweeted_status.get("id"),
                    "id_str": retweeted_status.get("id_str"),
                    "text": retweeted_status.get("text"),
                    "user": {
                        "id": retweeted_user_info.get("id"),
                        "id_str": retweeted_user_info.get("id_str"),
                        "name": retweeted_user_info.get("name"),
                        "screen_name": retweeted_user_info.get("screen_name")
                    },
                    "retweet_count": retweeted_status.get("retweet_count"),
                    "favorite_count": retweeted_status.get("favorite_count"),
                    "favorited": retweeted_status.get("favorited"),
                    "retweeted": retweeted_status.get("retweeted"),
                    "possibly_sensitive": retweeted_status.get("possibly_sensitive"),
                    "engagement_score1": engagement_score1
                } if retweeted_status else {},
                "retweet_count": tweet.get("retweet_count"),
                "favorite_count": tweet.get("favorite_count"),
                "favorited": tweet.get("favorited"),
                "retweeted": tweet.get("retweeted"),
                "possibly_sensitive": tweet.get("possibly_sensitive"),
                "engagement_score2": engagement_score2
            }
    
    return prepared_tweet

In [19]:
def index_tweet(tweet):
    res = es.index(index=index_name, id=tweet["id"], document=tweet)
    #print(f"Indexed Tweet ID: {tweet['id']} Status: {res['result']}")


In [20]:
def insert_user_mysql(user):
    cursor.execute(insert_sql, (
                    user['id_str'],
                    user['name'],
                    user['screen_name'],
                    user['location'],
                    user['verified'],
                    user['followers_count'],
                    user['statuses_count'],
                    user['friends_count']
                ))
                # Commit the transaction
  #  print("insert successfull")
    return 

In [21]:
import time
start_time = time.time()
# Read the file and index each tweet

with connection.cursor() as cursor:
    with open("/Users/layakishorereddy/Desktop/Rutgers/Dbms/Final Project/corona-out-2", 'r') as file:
        for line in file:

            if not line.strip():
                continue

            tweet = json.loads(line.strip())
            tweet_id = tweet.get("id_str")

            if es.exists(index=index_name_tweetids, id=tweet_id):
                    print(f"Tweet ID {tweet_id} already exists.")
                    continue

            es.index(index=index_name_tweetids, id=tweet_id, document={"tweet_id": tweet_id})

            user_info = tweet.get("user", {})
            retweeted_status = tweet.get("retweeted_status", {})
            retweeted_user_info = retweeted_status.get("user", {}) if retweeted_status else {}



            if ( tweet['text'].startswith('RT') ):

                #check if user is there or not
                user_id=user_info.get("id_str")
                cursor.execute(check_sql, (user_id,))
                result = cursor.fetchone()
                if result['COUNT(*)'] == 0:
                    insert_user_mysql(user_info)
                    connection.commit()
               #     print("commit success")
                    #if not load user into user index of es
                    # load or update user info in mysql
                    
                isretweet=True
                prepared_tweet=preparedTweet(tweet,user_info,retweeted_status,retweeted_user_info,isretweet)
                index_tweet(prepared_tweet)
                
                #check if Retweetuser is there or not
                if retweeted_status:
                   
                    tweet_id = retweeted_status.get("id_str")
                    if es.exists(index=index_name_tweetids, id=tweet_id):
                        print(f"Tweet ID {tweet_id} already exists.")
                        continue
                    else:
                        Ruser_id=retweeted_user_info.get("id_str")
                        cursor.execute(check_sql, (Ruser_id,))
                        result = cursor.fetchone()
                        if result['COUNT(*)'] == 0:
                            insert_user_mysql(retweeted_user_info)
                            connection.commit()
                        #    print("commit success")
                        #create a new original tweet for the retweet
                        isretweet=False
                        rc=retweeted_status.get("retweet_count")
                        lc=retweeted_status.get("favorite_count")
                        engagement_score2=(rc*rc)+lc
                        prepared_tweet=preparedTweet(tweet=retweeted_status,user_info=retweeted_user_info,retweeted_status={},retweeted_user_info={},isretweet=isretweet,engagement_score1=0,engagement_score2=engagement_score2)
                 #       print(prepared_tweet["engagement_score2"])
                        index_tweet(prepared_tweet)
                        print("Creating Original tweet")
                 
                else:
                    print(f"abnormal tweet ID {tweet_id}")
                    continue



            else:

                #check if user is there or not
                user_id=user_info.get("id_str")
                cursor.execute(check_sql, (user_id,))
                result = cursor.fetchone()
                if result['COUNT(*)'] == 0:
                    insert_user_mysql(user_info)
                    connection.commit()
              #      print("commit success")
                    #if not load user into user index of es
                    # load or update user info in mysql

                #load info into new table, tweetid, userid,screen_name, text, creationtime, retweet_count, Fav_count, retweeted, favourited, 
                #isretweet=false, Rtweetid, Ruserid,screen_name, Rcreationtime, retweet_count, Fav_count, retweeted, favourited

                #load info into main table
                isretweet=False
                rc=tweet.get("retweet_count")
                lc=tweet.get("favorite_count")
                engagement_score2=(rc*rc)+lc
                prepared_tweet=preparedTweet(tweet=tweet,user_info=user_info,retweeted_status=retweeted_status,retweeted_user_info=retweeted_user_info,isretweet=isretweet,engagement_score1=0,engagement_score2=engagement_score2)
               # print(prepared_tweet["engagement_score2"])
                index_tweet(prepared_tweet)





            #es.index(index=index_name_tweetids, id=tweet_id, document={"tweet_id": tweet_id, "user_id": user_id})

connection.close()
end_time = time.time()  # Capture end time
print(f"Total runtime of the program is {end_time - start_time} seconds")
print("All tweets have been indexed.")

insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull

insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert succes

insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Tweet ID 1249403835463811072 already exists.
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Or

Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert succes

Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Crea

...

Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Tweet ID 1249406345616461827 already exists.
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1249407255780511746 already exists.
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert su

insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Tweet ID 1249408515338313728 already exists.
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1249408655671386115 already exists.
insert successfull
Tweet ID 1249404442295894018 already exists.
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Tweet ID 1249408194562097155 already exists.
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Tweet ID 1249408209368072194 already exists.
Creating Original twee

insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
Tweet ID 1249408494316462080 already exists.
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1249405274995245056 already exists.
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1249407562115698688 already exists.
insert successfull
Tweet ID 1249408088576266240 already exists.
Tweet ID 1249408194562097155 already exists.
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Tweet ID 1249407988558974976 already exists.
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1249407548211564545 already exists.
ins

Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1249405169231675394 already exists.
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
Tweet ID 1249405407904358400 already exists.
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1249407745037647873 already exists.
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Tweet ID 1249405274995245056 already exists.
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull


Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Tweet ID 1249408778178420736 already exists.
insert successfull
Creating Original tweet
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1249408481532280832 already exists.
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1249403812864856065 already exists.
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1249407864944369665 already exists.
Tweet ID 1249408194562097155 already exists.
insert successfull
insert successfull
Creating Ori

In [24]:
import time
start_time = time.time()
# Read the file and index each tweet

with connection.cursor() as cursor:
    with open("/Users/layakishorereddy/Desktop/Rutgers/Dbms/Final Project/corona-out-3", 'r') as file:
        for line in file:

            if not line.strip():
                continue

            tweet = json.loads(line.strip())
            tweet_id = tweet.get("id_str")

            if es.exists(index=index_name_tweetids, id=tweet_id):
                    print(f"Tweet ID {tweet_id} already exists.")
                    continue

            es.index(index=index_name_tweetids, id=tweet_id, document={"tweet_id": tweet_id})

            user_info = tweet.get("user", {})
            retweeted_status = tweet.get("retweeted_status", {})
            retweeted_user_info = retweeted_status.get("user", {}) if retweeted_status else {}



            if ( tweet['text'].startswith('RT') ):

                #check if user is there or not
                user_id=user_info.get("id_str")
                cursor.execute(check_sql, (user_id,))
                result = cursor.fetchone()
                if result['COUNT(*)'] == 0:
                    insert_user_mysql(user_info)
                    connection.commit()
               #     print("commit success")
                    #if not load user into user index of es
                    # load or update user info in mysql
                    
                isretweet=True
                prepared_tweet=preparedTweet(tweet,user_info,retweeted_status,retweeted_user_info,isretweet)
                index_tweet(prepared_tweet)
                
                #check if Retweetuser is there or not
                if retweeted_status:
                   
                    tweet_id = retweeted_status.get("id_str")
                    if es.exists(index=index_name_tweetids, id=tweet_id):
                        print(f"Tweet ID {tweet_id} already exists.")
                        continue
                    else:
                        Ruser_id=retweeted_user_info.get("id_str")
                        cursor.execute(check_sql, (Ruser_id,))
                        result = cursor.fetchone()
                        if result['COUNT(*)'] == 0:
                            insert_user_mysql(retweeted_user_info)
                            connection.commit()
                        #    print("commit success")
                        #create a new original tweet for the retweet
                        isretweet=False
                        rc=retweeted_status.get("retweet_count")
                        lc=retweeted_status.get("favorite_count")
                        engagement_score2=(rc*rc)+lc
                        prepared_tweet=preparedTweet(tweet=retweeted_status,user_info=retweeted_user_info,retweeted_status={},retweeted_user_info={},isretweet=isretweet,engagement_score1=0,engagement_score2=engagement_score2)
                 #       print(prepared_tweet["engagement_score2"])
                        index_tweet(prepared_tweet)
                        print("Creating Original tweet")
                 
                else:
                    print(f"abnormal tweet ID {tweet_id}")
                    continue



            else:

                #check if user is there or not
                user_id=user_info.get("id_str")
                cursor.execute(check_sql, (user_id,))
                result = cursor.fetchone()
                if result['COUNT(*)'] == 0:
                    insert_user_mysql(user_info)
                    connection.commit()
              #      print("commit success")
                    #if not load user into user index of es
                    # load or update user info in mysql

                #load info into new table, tweetid, userid,screen_name, text, creationtime, retweet_count, Fav_count, retweeted, favourited, 
                #isretweet=false, Rtweetid, Ruserid,screen_name, Rcreationtime, retweet_count, Fav_count, retweeted, favourited

                #load info into main table
                isretweet=False
                rc=tweet.get("retweet_count")
                lc=tweet.get("favorite_count")
                engagement_score2=(rc*rc)+lc
                prepared_tweet=preparedTweet(tweet=tweet,user_info=user_info,retweeted_status=retweeted_status,retweeted_user_info=retweeted_user_info,isretweet=isretweet,engagement_score1=0,engagement_score2=engagement_score2)
               # print(prepared_tweet["engagement_score2"])
                index_tweet(prepared_tweet)





            #es.index(index=index_name_tweetids, id=tweet_id, document={"tweet_id": tweet_id, "user_id": user_id})

connection.close()
end_time = time.time()  # Capture end time
print(f"Total runtime of the program is {end_time - start_time} seconds")
print("All tweets have been indexed.")

Tweet ID 1254022770679320576 already exists.
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Origina

Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert s

insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating

insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
ins

insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Tweet ID 1254022867185999872 already exists.
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Tweet ID 1254022838903808000 already exists.
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert success

...

insert successfull
Tweet ID 1254048533080129540 already exists.
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Tweet ID 1254027175122153479 already exists.
insert successfull
Tweet ID 1254057082250072064 already exists.
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1254044888963874816 already exists.
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1254045905252167681 already exists.
insert successfull
Tweet ID 1254051862359289863 already exists.
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1254037158639415297 already exists.
insert successfull
Tweet ID 1254058124027322368 already exists.
insert successfull
Tweet ID 12

Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1254056716611645440 already exists.
insert successfull
Tweet ID 1254024862261280769 already exists.
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
Creating Original tweet
Tweet ID 1254039105085804544 already exists.
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
Tweet ID 1254059018999513089 already exists.
insert successfull
Tweet ID 1254035225912307712 already exists.
insert successfull
Tweet ID 1254057265910464513 already exists.
insert successfull
Tweet ID 1254051909356457991 already exists.
insert successfull
Tweet ID 1254056593504833539 already exists.
insert successfull
insert successfull
Creating Origina

Creating Original tweet
insert successfull
Tweet ID 1254059502002937864 already exists.
insert successfull
Tweet ID 1254030161403674624 already exists.
Tweet ID 1254058015365361665 already exists.
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Tweet ID 1254059502002937864 already exists.
insert successfull
insert successfull
Tweet ID 1254050406507954179 already exists.
insert successfull
Tweet ID 1254059193591627778 already exists.
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1254044919217479682 already exists.
insert successfull
Tweet ID 1254059018999513089 already exists.
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1254037192952995840 already exists.
insert successfull
Creating Original tweet
insert su

Tweet ID 1254047961258102785 already exists.
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1254028244166356998 already exists.
insert successfull
Tweet ID 1254057953042280451 already exists.
insert successfull
Creating Original tweet
insert successfull
insert successfull
Tweet ID 1254054317146935297 already exists.
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
insert successfull
Creating Original tweet
Creating Original tweet
insert successfull
Tweet ID 1254055206196703234 already exists.
insert successfull
Tweet ID 1254045905252167681 already exists.
insert successfull
insert successfull
Tweet ID 125405

insert successfull
insert successfull
Tweet ID 1254045251259564033 already exists.
insert successfull
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1254028244166356998 already exists.
Tweet ID 1254054965452189697 already exists.
insert successfull
Creating Original tweet
insert successfull
Tweet ID 1254058967480840198 already exists.
insert successfull
Tweet ID 1254050356042006529 already exists.
insert successfull
Creating Original tweet
insert successfull
insert successfull
Tweet ID 1254058312452182018 already exists.
Creating Original tweet
insert successfull
Creating Original tweet
insert successfull
insert successfull
insert successfull
Creating Original tweet
insert successfull
insert successfull
Tweet ID 1254058600856780801 already exists.
Tweet ID 1254045596266098695 already exists.
insert successfull
insert

# Searching by string or hashtags

In [28]:
def search_tweets(query_string, start_date=None, end_date=None):
    # Prepare the base query with necessary filters
    base_filter = [
        {"term": {"isretweet": False}}  # Filter to exclude retweets
    ]

    # Check if start_date and end_date are provided and append date range filter
    if start_date and end_date:
        base_filter.append({
            "range": {
                "created_at": {
                    "gte": start_date,  # Greater than or equal to start_date
                    "lte": end_date,    # Less than or equal to end_date
                    "format": "yyyy-MM-dd"  # Ensure your dates are in this format or change it accordingly
                }
            }
        })

    # Define the query using the updated filter list
    query = {
        "query": {
            "function_score": {
                "query": {
                    "bool": {
                        "must": {
                            "match": {
                                "text": query_string
                            }
                        },
                        "filter": {
                            "term": {
                                "isretweet": False
                            }
                        }
                    }
                },
                "functions": [
                    {
                        "field_value_factor": {
                            "field": "engagement_score2",
                            "factor": 1.2,
                            "modifier": "sqrt",
                            "missing": 1
                        }
                    }
                ],
                "boost_mode": "sum"
            }
        },
        "_source": ["created_at", "user.name", "text", "id_str", "retweet_count", "favorite_count", "engagement_score2"],
        "size": 10
    }
    
    # Perform the search using the defined query
    results = es.search(index=index_name, body=query)  # Replace 'index_name' with the name of your index
    print("Search Results:\n" + "-"*80)
    for hit in results['hits']['hits']:
        tweet_data = hit['_source']
        score = hit['_score'] 
        print(f"Tweet ID: {tweet_data.get('id_str')}")
        print(f"Username: {tweet_data['user']['name']}")
        print(f"Created At: {tweet_data['created_at']}")
        print(f"Text: {tweet_data['text']}")
        print(f"Retweets: {tweet_data.get('retweet_count', 0)}")
        print(f"Likes: {tweet_data.get('favorite_count', 0)}")
        print(f"Engagement Score2: {tweet_data.get('engagement_score2', 'Not available')}")
        print(f"Combined Relevance Score: {score}")
        print("-"*80)

# Example usage
import time
start_time = time.time()
search_tweets("Corona", "2020-01-01", "2022-12-31")
end_time = time.time()
print(f"Total runtime of the program is {end_time - start_time} seconds")


Search Results:
--------------------------------------------------------------------------------
Tweet ID: 1235256530728972290
Username: Pre K ❄️
Created At: Wed Mar 04 17:31:21 +0000 2020
Text: ALERT‼️‼️‼️
The corona virus can be spread through money. If you have any money at home, put on some gloves, put al… https://t.co/juJjDpFN3I
Retweets: 298538
Likes: 1128502
Engagement Score2: 89126065946
Combined Relevance Score: 327034.53
--------------------------------------------------------------------------------
Tweet ID: 1238264431320215553
Username: gilbert🚀
Created At: Fri Mar 13 00:43:40 +0000 2020
Text: *corona virus enters my body*

The 4 Flintstone gummies I ate in 2005: https://t.co/3STfdIQtaT
Retweets: 237307
Likes: 811062
Engagement Score2: 56315423311
Combined Relevance Score: 259959.23
--------------------------------------------------------------------------------
Tweet ID: 1240334979701395458
Username: D i l l 🦦
Created At: Wed Mar 18 17:51:18 +0000 2020
Text: When this Cor

# Searching a user based on string

In [29]:
import pymysql.cursors
from elasticsearch import Elasticsearch

def search_user_string(search_string):

    user_ids = []

    if search_string:
        # Elasticsearch query to find relevant user_ids
        query_body = {
            "query": {
                "bool": {
                    "must_not": [
                        {"exists": {"field": "retweeted_status"}}
                    ],
                    "should": [
                        {"match_phrase_prefix": {"user.name": {"query": search_string, "max_expansions": 50}}},
                        {"wildcard": {"user.screen_name": f"*{search_string}*"}}
                    ],
                    "minimum_should_match": 1
                }
            },
            "_source": ["user.id_str"],
            "size": 1000  # Adjust size if necessary
        }
        response = es.search(index=index_name, body=query_body)
        user_ids = [hit['_source']['user']['id_str'] for hit in response['hits']['hits']]

    if not user_ids:
        print("No user found with the given information.")
        return

    # Connect to MySQL using pymysql
    connection = pymysql.connect(host='localhost',
                                 user='root',
                                 password='layakishore',
                                 database='USERS_DATA',
                                 cursorclass=pymysql.cursors.DictCursor)
    try:
        with connection.cursor() as cursor:
            # MySQL query to fetch user details using a dynamic query for variable length user_ids
            format_strings = ','.join('%s' for _ in user_ids)
            query = f"""
            SELECT id, name, screen_name, location, verified, followers_count, statuses_count, friends_count
            FROM Users4
            WHERE id IN ({format_strings})
            ORDER BY FIELD(id, {','.join(user_ids)}), followers_count DESC
            """
            cursor.execute(query, tuple(user_ids))

            # Print user details
            results = cursor.fetchall()
            if results:
                for result in results:
                    print(f"ID: {result['id']}")
                    print(f"Name: {result['name']}")
                    print(f"Screen Name: {result['screen_name']}")
                    print(f"Location: {result['location']}")
                    print(f"Verified: {'Yes' if result['verified'] else 'No'}")
                    print(f"Followers Count: {result['followers_count']}")
                    print(f"Statuses Count: {result['statuses_count']}")
                    print(f"Friends Count: {result['friends_count']}")
                    print("-" * 40)
            else:
                print("No user found with the given IDs in MySQL.")
    finally:
        connection.close()

#Example usage
search_user_string(search_string="gol")


ID: 8724992
Name: Golem.de
Screen Name: golem
Location: Berlin, Germany
Verified: Yes
Followers Count: 79498
Statuses Count: 92346
Friends Count: 0
----------------------------------------
ID: 1094510241386037248
Name: goldengreek
Screen Name: goldengreek0
Location: None
Verified: No
Followers Count: 627
Statuses Count: 11614
Friends Count: 153
----------------------------------------
ID: 41349962
Name: gol
Screen Name: goldieaishawrt
Location: ÜT: -6.202799,106.88672
Verified: No
Followers Count: 331
Statuses Count: 5763
Friends Count: 254
----------------------------------------
ID: 3352950015
Name: GoldieZman
Screen Name: goldieZman
Location: None
Verified: No
Followers Count: 61
Statuses Count: 2190
Friends Count: 44
----------------------------------------
ID: 1232282021709283334
Name: GoldenPhavil88
Screen Name: Phapha565532289
Location: None
Verified: No
Followers Count: 0
Statuses Count: 1653
Friends Count: 0
----------------------------------------
ID: 952192862283862016
Name:

# Searching all the retweets and tweets made by a User

In [11]:
def search_user_tweets(user_id):
    query = {
        "query": {
            "bool": {
                "must": [
                    {"term": {"user.id_str": user_id}}  # Filter to match the user ID
                ]
            }
        },
        "sort": [
            {"created_at": {"order": "asc"}}  # Sort the tweets by creation date in ascending order
        ],
        "_source": [
            "created_at", "user.name", "text", "isretweet", "retweet_count", "favorite_count", "retweeted_status"
        ]  # Include retweet and like counts, and retweeted_status for extracting counts if it is a retweet
    }
    
    # Execute the search query
    results = es.search(index=index_name, body=query)#, size=1000)  # Adjust size as needed
    print("Search Results:\n" + "-"*80)  # Print a header and a separator
    for hit in results['hits']['hits']:
        # Extracting the specified fields from each tweet
        tweet_data = hit['_source']
        print(f"Tweet ID: {hit['_id']}")  # Using the document ID as Tweet ID
        print(f"Username: {tweet_data['user']['name']}")
        print(f"Created At: {tweet_data['created_at']}")
        print(f"Text: {tweet_data['text']}")

        # Check if the tweet is a retweet and extract like and retweet counts accordingly
        if tweet_data.get('isretweet', False):
            retweet_data = tweet_data.get('retweeted_status', {})
            retweet_count = retweet_data.get('retweet_count', 0)
            favorite_count = retweet_data.get('favorite_count', 0)
        else:
            retweet_count = tweet_data.get('retweet_count', 0)
            favorite_count = tweet_data.get('favorite_count', 0)

        print(f"Retweets: {retweet_count}")
        print(f"Likes: {favorite_count}")
        print(f"Is Retweet: {'Yes' if tweet_data.get('isretweet', False) else 'No'}")
        print("-"*80)  # Print a line after each tweet's details

# Example usage
start_time = time.time()
user_id = "1013800044695179265"
search_user_tweets("1013800044695179265")
end_time = time.time()
print(f"Total runtime of the program is {end_time - start_time} seconds")


Search Results:
--------------------------------------------------------------------------------
Tweet ID: 1249403775632076801
Username: DavidGultomteknisilistrik
Created At: Sun Apr 12 18:27:27 +0000 2020
Text: RT @detikcom: Seorang pria tiba-tiba tergeletak di trotoar Medan. Pria itu kemudian dievakuasi dengan menggunakan protokol penanganan virus…
Retweets: 10
Likes: 48
Is Retweet: Yes
--------------------------------------------------------------------------------
Total runtime of the program is 0.05240583419799805 seconds


# Searching a user based on user id

In [13]:
import pymysql.cursors

def search_user_by_id(user_id):
    # Establish a database connection using pymysql
    connection = pymysql.connect(
        host='localhost',
        user='root',
        password='layakishore',
        database='USERS_DATA',
        cursorclass=pymysql.cursors.DictCursor
    )
    
    try:
        with connection.cursor() as cursor:
            # Prepare the query
            query = """
            SELECT id, name, screen_name, location, verified, followers_count, statuses_count, friends_count
            FROM Users4
            WHERE id = %s
            """
    
            # Execute the query with the provided user ID
            cursor.execute(query, (user_id,))
    
            # Fetch and print all the results
            results = cursor.fetchall()
            if results:
                for result in results:
                    print(f"ID: {result['id']}")
                    print(f"Name: {result['name']}")
                    print(f"Screen Name: {result['screen_name']}")
                    print(f"Location: {result['location']}")
                    print(f"Verified: {'Yes' if result['verified'] else 'No'}")
                    print(f"Followers Count: {result['followers_count']}")
                    print(f"Statuses Count: {result['statuses_count']}")
                    print(f"Friends Count: {result['friends_count']}")
                    print("-" * 40)
            else:
                print("No user found with the given user ID.")
    finally:
        connection.close()

# Example usage
search_user_by_id('841961917807767553')


ID: 841961917807767553
Name: Adarsh Saxena
Screen Name: AdarshSaxena74
Location: Jaipur, India
Verified: No
Followers Count: 331
Statuses Count: 1235
Friends Count: 246
----------------------------------------


# Searching all the Users who retweeted a particular Tweet

In [21]:
import pymysql.cursors
from elasticsearch import Elasticsearch

def find_retweeters_and_print_details(tweet_id):
    tweet_id=get_original_tweet_id(tweet_id)
    user_ids = set()

    # Fetch the original tweet details
    original_query = {
        "query": {
            "term": {"id_str": tweet_id}
        },
        "_source": ["id_str", "text", "user.id_str","favorite_count","retweet_count"],
        "size": 1
    }
    original_response = es.search(index=index_name, body=original_query)

    original_tweet = None
    if original_response['hits']['hits']:
        original_tweet = original_response['hits']['hits'][0]
        original_tweet_user_id = original_tweet['_source']['user']['id_str']
        user_ids.add(original_tweet_user_id)

    # Fetch all retweets of the given tweet_id
    retweet_query = {
        "query": {
            "term": {"retweeted_status.id_str": tweet_id}
        },
        "_source": ["id_str", "text", "user.id_str","favorite_count","retweet_count"],
        "size": 1000
    }
    retweet_response = es.search(index=index_name, body=retweet_query)

    if retweet_response['hits']['hits']:
        for hit in retweet_response['hits']['hits']:
            user_id = hit['_source']['user']['id_str']
            user_ids.add(user_id)

    # Ensure there are user IDs to query in MySQL
    if not user_ids:
        print("No user details to fetch.")
        return

    # Connect to MySQL using pymysql
    connection = pymysql.connect(host='localhost',
                                 user='root',
                                 password='layakishore',
                                 database='USERS_DATA',
                                 cursorclass=pymysql.cursors.DictCursor)
    try:
        with connection.cursor() as cursor:
            # MySQL query to fetch user details
            format_strings = ','.join(['%s'] * len(user_ids))  # Ensures the correct number of placeholders
            query = f"""
            SELECT id, name, screen_name, location, verified, followers_count, statuses_count, friends_count
            FROM Users4
            WHERE id IN ({format_strings})
            """
            cursor.execute(query, tuple(user_ids))
            results = cursor.fetchall()

            # Dictionary to store user info for easy access
            users_info = {result['id']: result for result in results}

            # Print details of the original tweet's user
            if original_tweet_user_id in users_info:
                print("Original Tweet User Info:\n" + "="*60)
                user = users_info[original_tweet_user_id]
                print_user_info(user)
                print("="*60)

            # Print original tweet details
            if original_tweet:
                print(f"Original Tweet ID: {original_tweet['_source']['id_str']}")
                print(f"Original Tweet Text: {original_tweet['_source']['text']}")
                print(f"Likes: {original_tweet['_source']['favorite_count']}")
                print(f"Retweets: {original_tweet['_source']['retweet_count']}")
                print("-" * 60)

            # Print retweet details
            if retweet_response['hits']['hits']:
                print(f"Retweets of Tweet ID {tweet_id}:\n" + "-"*60)
                for hit in retweet_response['hits']['hits']:
                    retweet_id = hit['_source']['id_str']
                    retweet_text = hit['_source']['text']
                    retweeted_user_id = hit['_source']['user']['id_str']
                    print(f"Retweet ID: {retweet_id}\nRetweet Text: {retweet_text}\nRetweeted by User ID: {retweeted_user_id}")
                    if retweeted_user_id in users_info:
                        print_user_info(users_info[retweeted_user_id])
                    print("-" * 60)
            else:
                print("No retweets found for this tweet ID.")
    finally:
        connection.close()

def print_user_info(user):
    if user:
        print(f"User ID: {user['id']}\nName: {user['name']}\nScreen Name: {user['screen_name']}")
        print(f"Location: {user['location']}\nVerified: {'Yes' if user['verified'] else 'No'}")
        print(f"Followers Count: {user['followers_count']}\nStatuses Count: {user['statuses_count']}\nFriends Count: {user['friends_count']}")

# Example usage

def get_original_tweet_id(tweet_id):
    
    # Query to fetch the tweet by ID
    query = {
        "query": {
            "term": {"id_str": tweet_id}
        },
        "_source": ["id_str", "isretweet", "retweeted_status.id_str"]
    }
    
    # Execute the search
    response = es.search(index=index_name, body=query)  # Replace "tweets_index" with your index name
    
    # Check if any tweet was found
    if response['hits']['hits']:
        tweet = response['hits']['hits'][0]['_source']
        
        # Check if the tweet is a retweet
        if tweet.get('isretweet', False):
            # Return the original tweet ID from the retweeted_status if available
            return tweet.get('retweeted_status', {}).get('id_str', tweet_id)
        else:
            # Return the provided tweet ID as it's not a retweet
            return tweet_id
    else:
        # No tweet found by the given ID
        return None
    
find_retweeters_and_print_details("1249403835468009472")





Original Tweet User Info:
User ID: 841961917807767553
Name: Adarsh Saxena
Screen Name: AdarshSaxena74
Location: Jaipur, India
Verified: No
Followers Count: 331
Statuses Count: 1235
Friends Count: 246
Original Tweet ID: 1249358229265498118
Original Tweet Text: सर आपकी इस हौसला अफजाई से PSUs में निश्चित रूप से नई ऊर्जा का संचार होगा l @dpradhanbjp @BSNLCorporate @OfficeOfRSP… https://t.co/Hig4taqmMZ
Likes: 12
Retweets: 12
------------------------------------------------------------
Retweets of Tweet ID 1249358229265498118:
------------------------------------------------------------
Retweet ID: 1249403827234541568
Retweet Text: RT @AdarshSaxena74: सर आपकी इस हौसला अफजाई से PSUs में निश्चित रूप से नई ऊर्जा का संचार होगा l @dpradhanbjp @BSNLCorporate @OfficeOfRSP @Ze…
Retweeted by User ID: 101007632
User ID: 101007632
Name: Ravin Gupta
Screen Name: IamRaavin
Location: india
Verified: No
Followers Count: 499
Statuses Count: 4038
Friends Count: 537
-------------------------------------------

# Top 10 Tweets (Ordering using the predefined metric)

In [18]:
from elasticsearch import Elasticsearch
import pymysql.cursors

# Establish connection to MySQL using pymysql
connection = pymysql.connect(host='localhost',
                             user='root',
                             password='layakishore',
                             database='USERS_DATA',
                             cursorclass=pymysql.cursors.DictCursor)


def fetch_user_details(user_id):
    with connection.cursor() as cursor:
        query = "SELECT name, screen_name, location, followers_count FROM users4 WHERE id = %s"
        cursor.execute(query, (user_id,))
        user_info = cursor.fetchone()
    return user_info

def Top_10_tweets():
    query = {
        "size": 10,
        "query": {
            "bool": {
                "must": [
                    {"match": {"isretweet": False}}
                ],
                
            }
        },
        "sort": [
            {"engagement_score2": {"order": "desc"}}  # Sorting by engagement_score2
        ]
    }
    results = es.search(index=index_name, body=query)
    print("Search Results:\n" + "-"*40)  # Print a header and a separator
    for result in results['hits']['hits']:
        tweet = result['_source']
        user_info = fetch_user_details(tweet['user']['id_str'])
        print(f"Tweet ID: {result['_id']}")
        print(f"Text: {tweet.get('text', 'No text available')}")
        print(f"Retweets: {tweet.get('retweet_count', 0)}")
        print(f"Likes: {tweet.get('favorite_count', 0)}")
        print(f"Engagement Score2: {tweet.get('engagement_score2', 'Not available')}")  # Display the engagement_score2
        print("User Info:")
        if user_info:
            print(f"Name: {user_info['name']}")
            print(f"Screen Name: {user_info['screen_name']}")
            print(f"Location: {user_info['location']}")
            print(f"Followers: {user_info['followers_count']}")
        else:
            print("User details not found.")
        print("-" * 40)

start_time = time.time()
Top_10_tweets()
end_time = time.time()
print(f"Total runtime of the program is {end_time - start_time} seconds")

# Close the database connection
connection.close()


Search Results:
----------------------------------------
Tweet ID: 1235256530728972290
Text: ALERT‼️‼️‼️
The corona virus can be spread through money. If you have any money at home, put on some gloves, put al… https://t.co/juJjDpFN3I
Retweets: 298538
Likes: 1128502
Engagement Score2: 89126065946
User Info:
Name: Pre K ❄️
Screen Name: stayfrea_
Location: Seattle, WA
Followers: 69322
----------------------------------------
Tweet ID: 1238264431320215553
Text: *corona virus enters my body*

The 4 Flintstone gummies I ate in 2005: https://t.co/3STfdIQtaT
Retweets: 237307
Likes: 811062
Engagement Score2: 56315423311
User Info:
Name: gilbert🚀
Screen Name: HtownBabyG
Location: Houston, TX
Followers: 672
----------------------------------------
Tweet ID: 1240334979701395458
Text: When this Corona shit passes we have to promise each other that we’re going to tell our kids that we survived a zombie apocalypse in 2020
Retweets: 181584
Likes: 764405
Engagement Score2: 32973513461
User Info:
Name: 

# Top 10 Users

In [29]:
import pymysql
import time

# Establishing connections
connection = pymysql.connect(host='localhost',
                             user='root',
                             password='layakishore',
                             database='USERS_DATA',
                             charset='utf8mb4',
                             cursorclass=pymysql.cursors.DictCursor)

def get_top_10_users_by_followers():
    """ Fetch top 10 users sorted by followers count from MySQL """
    with connection.cursor() as cursor:
        # Query to fetch users sorted by followers count in descending order
        cursor.execute("SELECT id, name, screen_name, followers_count FROM users4 ORDER BY followers_count DESC LIMIT 10")
        top_users = cursor.fetchall()  # Fetches the top 10 users
        return top_users

def print_user_details(top_users):
    """ Print details of top users """
    print("Top 10 Users by Followers Count:\n" + "-" * 40)
    for user in top_users:
        print(f"User ID: {user['id']}")
        print(f"Name: {user['name']}")
        print(f"Screen Name: {user['screen_name']}")
        print(f"Followers Count: {user['followers_count']}")
        print("-" * 40)

# Main execution flow
start_time = time.time()
top_users = get_top_10_users_by_followers()
print_user_details(top_users)
end_time = time.time()
print(f"Total runtime of the program is {end_time - start_time} seconds")

# Closing the database connection
connection.close()


Top 10 Users by Followers Count:
----------------------------------------
User ID: 813286
Name: Barack Obama
Screen Name: BarackObama
Followers Count: 115603427
----------------------------------------
User ID: 18839785
Name: Narendra Modi
Screen Name: narendramodi
Followers Count: 55406011
----------------------------------------
User ID: 807095
Name: The New York Times
Screen Name: nytimes
Followers Count: 46361159
----------------------------------------
User ID: 145125358
Name: Amitabh Bachchan
Screen Name: SrBachchan
Followers Count: 41596464
----------------------------------------
User ID: 101311381
Name: Shah Rukh Khan
Screen Name: iamsrk
Followers Count: 40026760
----------------------------------------
User ID: 471741741
Name: PMO India
Screen Name: PMOIndia
Followers Count: 33756093
----------------------------------------
User ID: 113419517
Name: Hrithik Roshan
Screen Name: iHrithik
Followers Count: 28170371
----------------------------------------
User ID: 92724677
Name: V

# Cache

In [13]:
import collections
import pickle
import os

class LRUCache:
    def __init__(self, capacity=10):
        self.cache = collections.OrderedDict()
        self.capacity = capacity

    def get(self, key):
        if key not in self.cache:
            return None
        # Move the key to the end to show that it was recently used
        self.cache.move_to_end(key)
        return self.cache[key]

    def put(self, key, value):
        if key in self.cache:
            # Move the key to the end to show that it was recently used
            self.cache.move_to_end(key)
        self.cache[key] = value
       # print("cache length= "+len(self.cache))
        # If the cache exceeds the capacity, remove the first item
        if len(self.cache) > self.capacity:
            self.cache.popitem(last=False)

    def save_to_disk(self, filename='cache.pkl'):
        with open(filename, 'wb') as f:
            pickle.dump(self.cache, f)

    def load_from_disk(self, filename='cache.pkl'):
        if os.path.exists(filename):
            with open(filename, 'rb') as f:
                self.cache = pickle.load(f)
                
    def print_all_keys(self):
        for key in self.cache.keys():
            print(key)

# Instantiate and load cache
cache = LRUCache(capacity=7)



In [13]:
import threading

def checkpoint_cache(cache, interval=60):
    def run():
        while True:
            time.sleep(interval)
            #print("awake")
            cache.save_to_disk()
            cache.load_from_disk()
    thread = threading.Thread(target=run)
    thread.daemon = True
    thread.start()


In [343]:
checkpoint_cache(cache)

awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake
awake


# Top 10 tweets(Using Cache)

In [14]:
from elasticsearch import Elasticsearch
import pymysql.cursors
import time

# Establish connections
connection = pymysql.connect(host='localhost',
                             user='root',
                             password='layakishore',
                             database='USERS_DATA',
                             cursorclass=pymysql.cursors.DictCursor)


def fetch_user_details(user_id):
    user_info = cache.get(f"user_{user_id}")
    if user_info:
        return user_info
    with connection.cursor() as cursor:
        query = "SELECT name, screen_name, location, followers_count FROM users4 WHERE id = %s"
        cursor.execute(query, (user_id,))
        user_info = cursor.fetchone()
        cache.put(f"user_{user_id}", user_info)
    return user_info

def Top_10_tweets():
    
    cached_tweets = cache.get('top_10_tweets')
    if cached_tweets:
        for tweet in cached_tweets:
            print_tweet_info(tweet)
        return

    query = {
        "size": 10,
        "query": {
            "bool": {
                "must": [
                    {"match": {"isretweet": False}}
                ],
            }
        },
        "sort": [
            {"engagement_score2": {"order": "desc"}}
        ]
    }
    results = es.search(index=index_name, body=query)
    tweets_info = []
    print("Search Results:\n" + "-"*40)
    for result in results['hits']['hits']:
        tweet = result['_source']
        user_info = fetch_user_details(tweet['user']['id_str'])
        tweet_info = {
            "tweet_id": result['_id'],
            "text": tweet.get('text', 'No text available'),
            "retweets": tweet.get('retweet_count', 0),
            "likes": tweet.get('favorite_count', 0),
            "engagement_score2": tweet.get('engagement_score2', 'Not available'),
            "user_info": user_info
        }
        tweets_info.append(tweet_info)
        print_tweet_info(tweet_info)

    cache.put('top_10_tweets', tweets_info)

def print_tweet_info(tweet):
    print(f"Tweet ID: {tweet['tweet_id']}")
    print(f"Text: {tweet['text']}")
    print(f"Retweets: {tweet['retweets']}")
    print(f"Likes: {tweet['likes']}")
    print(f"Engagement Score2: {tweet['engagement_score2']}")
    print("User Info:")
    if tweet['user_info']:
        user_info = tweet['user_info']
        print(f"Name: {user_info['name']}")
        print(f"Screen Name: {user_info['screen_name']}")
        print(f"Location: {user_info['location']}")
        print(f"Followers: {user_info['followers_count']}")
    print("-" * 40)

start_time = time.time()
Top_10_tweets()
end_time = time.time()
print(f"Total runtime of the program is {end_time - start_time} seconds")

# Close the database connection
connection.close()




Search Results:
----------------------------------------
Tweet ID: 1235256530728972290
Text: ALERT‼️‼️‼️
The corona virus can be spread through money. If you have any money at home, put on some gloves, put al… https://t.co/juJjDpFN3I
Retweets: 298538
Likes: 1128502
Engagement Score2: 89126065946
User Info:
Name: Pre K ❄️
Screen Name: stayfrea_
Location: Seattle, WA
Followers: 69322
----------------------------------------
Tweet ID: 1238264431320215553
Text: *corona virus enters my body*

The 4 Flintstone gummies I ate in 2005: https://t.co/3STfdIQtaT
Retweets: 237307
Likes: 811062
Engagement Score2: 56315423311
User Info:
Name: gilbert🚀
Screen Name: HtownBabyG
Location: Houston, TX
Followers: 672
----------------------------------------
Tweet ID: 1240334979701395458
Text: When this Corona shit passes we have to promise each other that we’re going to tell our kids that we survived a zombie apocalypse in 2020
Retweets: 181584
Likes: 764405
Engagement Score2: 32973513461
User Info:
Name: 

# Searching by string or hashtags(Using Cache)

In [26]:
from elasticsearch import Elasticsearch
import time



def search_tweets(query_string):
    cache_key = f"search_{query_string}"
    cached_results = cache.get(cache_key)
    
    if cached_results:
        print("Using cached results for:", query_string)
        print_search_results(cached_results)
        return
    
    query = {
        "query": {
            "function_score": {
                "query": {
                    "bool": {
                        "must": {
                            "match": {
                                "text": query_string
                            }
                        },
                        "filter": {
                            "term": {
                                "isretweet": False
                            }
                        }
                    }
                },
                "functions": [
                    {
                        "field_value_factor": {
                            "field": "engagement_score2",
                            "factor": 1.2,
                            "modifier": "sqrt",
                            "missing": 1
                        }
                    }
                ],
                "boost_mode": "sum"
            }
        },
        "_source": ["created_at", "user.name", "text", "id_str", "retweet_count", "favorite_count", "engagement_score2"],
        "size": 10
    }
    
    results = es.search(index=index_name, body=query)
    formatted_results = format_search_results(results)
    cache.put(cache_key, formatted_results)  # Cache the new results
    print_search_results(formatted_results)

def format_search_results(results):
    return [{
        "id_str": hit['_source'].get('id_str'),
        "username": hit['_source']['user']['name'],
        "created_at": hit['_source']['created_at'],
        "text": hit['_source']['text'],
        "retweets": hit['_source'].get('retweet_count', 0),
        "likes": hit['_source'].get('favorite_count', 0),
        "engagement_score2": hit['_source'].get('engagement_score2', 'Not available'),
        "score": hit['_score']
    } for hit in results['hits']['hits']]

def print_search_results(results):
    print("Search Results:\n" + "-"*80)
    for result in results:
        print(f"Tweet ID: {result['id_str']}")
        print(f"Username: {result['username']}")
        print(f"Created At: {result['created_at']}")
        print(f"Text: {result['text']}")
        print(f"Retweets: {result['retweets']}")
        print(f"Likes: {result['likes']}")
        print(f"Engagement Score2: {result['engagement_score2']}")
        print(f"Combined Relevance Score: {result['score']}")
        print("-"*80)

# Example usage
start_time = time.time()
search_tweets("corona")
end_time = time.time()
print(f"Total runtime of the program is {end_time - start_time} seconds")


Search Results:
--------------------------------------------------------------------------------
Tweet ID: 1235256530728972290
Username: Pre K ❄️
Created At: Wed Mar 04 17:31:21 +0000 2020
Text: ALERT‼️‼️‼️
The corona virus can be spread through money. If you have any money at home, put on some gloves, put al… https://t.co/juJjDpFN3I
Retweets: 298538
Likes: 1128502
Engagement Score2: 89126065946
Combined Relevance Score: 327034.53
--------------------------------------------------------------------------------
Tweet ID: 1238264431320215553
Username: gilbert🚀
Created At: Fri Mar 13 00:43:40 +0000 2020
Text: *corona virus enters my body*

The 4 Flintstone gummies I ate in 2005: https://t.co/3STfdIQtaT
Retweets: 237307
Likes: 811062
Engagement Score2: 56315423311
Combined Relevance Score: 259959.23
--------------------------------------------------------------------------------
Tweet ID: 1240334979701395458
Username: D i l l 🦦
Created At: Wed Mar 18 17:51:18 +0000 2020
Text: When this Cor

# Searching all the retweets and tweets made by a User(Using Cache)

In [77]:
def search_user_tweets(user_id):
    cache_key = f"user_tweets_{user_id}"
    cached_tweets = cache.get(cache_key)
    
    if cached_tweets:
        print("Using cached results for user ID:", user_id)
        print_search_results(cached_tweets)
        return

    query = {
        "query": {
            "bool": {
                "must": [
                    {"term": {"user.id_str": user_id}}
                ]
            }
        },
        "sort": [
            {"created_at": {"order": "asc"}}
        ],
        "_source": [
            "created_at", "user.name", "text", "isretweet", "retweet_count", "favorite_count", "retweeted_status"
        ],
        "size": 100  # Adjust based on your needs
    }
    
    results = es.search(index=index_name, body=query)
    formatted_results = format_tweet_results(results)
    cache.put(cache_key, formatted_results)  # Cache the results
    print_search_results(formatted_results)

def format_tweet_results(results):
    return [{
        "id": hit['_id'],
        "username": hit['_source']['user']['name'],
        "created_at": hit['_source']['created_at'],
        "text": hit['_source']['text'],
        "retweets": hit['_source'].get('retweet_count', 0),
        "likes": hit['_source'].get('favorite_count', 0),
        "is_retweet": hit['_source'].get('isretweet', False)
    } for hit in results['hits']['hits']]

def print_search_results(tweets):
    print("Search Results:\n" + "-"*80)
    for tweet in tweets:
        print(f"Tweet ID: {tweet['id']}")
        print(f"Username: {tweet['username']}")
        print(f"Created At: {tweet['created_at']}")
        print(f"Text: {tweet['text']}")
        print(f"Retweets: {tweet['retweets']}")
        print(f"Likes: {tweet['likes']}")
        print(f"Is Retweet: {'Yes' if tweet['is_retweet'] else 'No'}")
        print("-"*80)

# Example usage

start_time = time.time()
user_id = "1240111705599991809"
search_user_tweets(user_id)
end_time = time.time()
print(f"Total runtime of the program is {end_time - start_time} seconds")

Using cached results for user ID: 1240111705599991809
Search Results:
--------------------------------------------------------------------------------
Tweet ID: 1249403803700322304
Username: Santosh Sharma
Created At: Sun Apr 12 18:27:34 +0000 2020
Text: RT @blsanthosh: She is Smt Srijana Gummala ... Greater Vishakaatnam Municipal Commissioner.... She returned to her work with her 1 month ol…
Retweets: 0
Likes: 0
Is Retweet: Yes
--------------------------------------------------------------------------------
Total runtime of the program is 0.00043010711669921875 seconds


# Searching a user based on string(Using Cache)

In [89]:
def search_user_string(search_string):
    cache_key = f"user_search_{search_string}"
    cached_results = cache.get(cache_key)
    
    if cached_results:
        print("Using cached results for search string:", search_string)
        print_user_details(cached_results)
        return
    
    user_ids = []

    if search_string:
        # Elasticsearch query to find relevant user_ids
        query_body = {
            "query": {
                "bool": {
                    "must_not": [
                        {"exists": {"field": "retweeted_status"}}
                    ],
                    "should": [
                        {"match_phrase_prefix": {"user.name": {"query": search_string, "max_expansions": 50}}},
                        {"wildcard": {"user.screen_name": f"*{search_string}*"}}
                    ],
                    "minimum_should_match": 1
                }
            },
            "_source": ["user.id_str"],
            "size": 1000  # Adjust size if necessary
        }
        response = es.search(index=index_name, body=query_body)
        user_ids = [hit['_source']['user']['id_str'] for hit in response['hits']['hits']]
    
    if not user_ids:
        print("No user found with the given information.")
        return

    connection = pymysql.connect(host='localhost',
                                 user='root',
                                 password='layakishore',
                                 database='USERS_DATA',
                                 cursorclass=pymysql.cursors.DictCursor)
    try:
        with connection.cursor() as cursor:
            format_strings = ','.join('%s' for _ in user_ids)
            query = f"""
            SELECT id, name, screen_name, location, verified, followers_count, statuses_count, friends_count
            FROM Users4
            WHERE id IN ({format_strings})
            """
            cursor.execute(query, tuple(user_ids))
            results = cursor.fetchall()
            if results:
                cache.put(cache_key, results)  # Cache the results
                print_user_details(results)
            else:
                print("No user found with the given IDs in MySQL.")
    finally:
        connection.close()

def print_user_details(results):
    for result in results:
        print(f"ID: {result['id']}")
        print(f"Name: {result['name']}")
        print(f"Screen Name: {result['screen_name']}")
        print(f"Location: {result['location']}")
        print(f"Verified: {'Yes' if result['verified'] else 'No'}")
        print(f"Followers Count: {result['followers_count']}")
        print(f"Statuses Count: {result['statuses_count']}")
        print(f"Friends Count: {result['friends_count']}")
        print("-" * 40)

# Example usage

start_time = time.time()
search_user_string("gol")
end_time = time.time()
print(f"Total runtime of the program is {end_time - start_time} seconds")

Using cached results for search string: gol
ID: 1021320773083041792
Name: Peter Ugolini-Schmidt
Screen Name: UgoliniPeter
Location: Berlin, Germany
Verified: No
Followers Count: 304
Statuses Count: 755
Friends Count: 430
----------------------------------------
ID: 1034700483477291008
Name: Gogol Lafit
Screen Name: GogolLafit
Location: Dorsten
Verified: No
Followers Count: 5296
Statuses Count: 40579
Friends Count: 5456
----------------------------------------
ID: 1036261033915105280
Name: GOLDEN BOY
Screen Name: Goldenb855
Location: None
Verified: No
Followers Count: 70
Statuses Count: 1768
Friends Count: 330
----------------------------------------
ID: 1065325422647418886
Name: Theatre  Gold Reviews
Screen Name: theatre_gold
Location: London, England
Verified: No
Followers Count: 117
Statuses Count: 1801
Friends Count: 352
----------------------------------------
ID: 1072609981793529856
Name: ana alice
Screen Name: halmoonlight
Location: None
Verified: No
Followers Count: 334
Statuses

# Searching a user based on user id(Using Cache)

In [81]:
import pymysql.cursors

# Assuming cache is an instance of LRUCache
def search_user_by_id(user_id):
    cache_key = f"user_details_{user_id}"
    cached_user = cache.get(cache_key)
    
    if cached_user:
        print("Using cached results for user ID:", user_id)
        print_user_details(cached_user)
        return
    
    # Establish a database connection using pymysql
    connection = pymysql.connect(
        host='localhost',
        user='root',
        password='layakishore',
        database='USERS_DATA',
        cursorclass=pymysql.cursors.DictCursor
    )
    
    try:
        with connection.cursor() as cursor:
            # Prepare the query
            query = """
            SELECT id, name, screen_name, location, verified, followers_count, statuses_count, friends_count
            FROM Users4
            WHERE id = %s
            """
    
            # Execute the query with the provided user ID
            cursor.execute(query, (user_id,))
    
            # Fetch the results
            results = cursor.fetchall()
            if results:
                cache.put(cache_key, results)  # Cache the results
                print_user_details(results)
            else:
                print("No user found with the given user ID.")
    finally:
        connection.close()

def print_user_details(results):
    for result in results:
        print(f"ID: {result['id']}")
        print(f"Name: {result['name']}")
        print(f"Screen Name: {result['screen_name']}")
        print(f"Location: {result['location']}")
        print(f"Verified: {'Yes' if result['verified'] else 'No'}")
        print(f"Followers Count: {result['followers_count']}")
        print(f"Statuses Count: {result['statuses_count']}")
        print(f"Friends Count: {result['friends_count']}")
        print("-" * 40)

# Example usage
start_time = time.time()
search_user_by_id('14135350')
end_time = time.time()
print(f"Total runtime of the program is {end_time - start_time} seconds")



Using cached results for user ID: 14135350
ID: 14135350
Name: Bianna Golodryga
Screen Name: biannagolodryga
Location: New York
Verified: Yes
Followers Count: 148430
Statuses Count: 13104
Friends Count: 3376
----------------------------------------
Total runtime of the program is 0.001188039779663086 seconds


# Searching all the Users who retweeted a particular Tweet(Using Cache)

In [83]:
import pymysql.cursors
from elasticsearch import Elasticsearch


def find_retweeters_and_print_details(tweet_id):
    cache_key = f"retweet_details_{tweet_id}"
    cached_data = cache.get(cache_key)
    
    if cached_data:
        print("Using cached results for tweet ID:", tweet_id)
        print_cached_tweet_details(cached_data)
        return
    
    original_tweet_id = get_original_tweet_id(tweet_id)
    user_ids = set()

    # Fetch the original tweet details
    original_query = {
        "query": {
            "term": {"id_str": original_tweet_id}
        },
        "_source": ["id_str", "text", "user.id_str", "favorite_count", "retweet_count"],
        "size": 1
    }
    original_response = es.search(index=index_name, body=original_query)

    original_tweet = None
    if original_response['hits']['hits']:
        original_tweet = original_response['hits']['hits'][0]
        original_tweet_user_id = original_tweet['_source']['user']['id_str']
        user_ids.add(original_tweet_user_id)

    # Fetch all retweets of the given tweet_id
    retweet_query = {
        "query": {
            "term": {"retweeted_status.id_str": original_tweet_id}
        },
        "_source": ["id_str", "text", "user.id_str", "favorite_count", "retweet_count"],
        "size": 1000
    }
    retweet_response = es.search(index=index_name, body=retweet_query)

    if retweet_response['hits']['hits']:
        for hit in retweet_response['hits']['hits']:
            user_id = hit['_source']['user']['id_str']
            user_ids.add(user_id)

    if not user_ids:
        print("No user details to fetch.")
        return

    # Fetch user details from MySQL
    connection = pymysql.connect(host='localhost',
                                 user='root',
                                 password='layakishore',
                                 database='USERS_DATA',
                                 cursorclass=pymysql.cursors.DictCursor)
    try:
        with connection.cursor() as cursor:
            format_strings = ','.join(['%s'] * len(user_ids))  # Ensures the correct number of placeholders
            query = f"SELECT id, name, screen_name, location, verified, followers_count, statuses_count, friends_count FROM Users4 WHERE id IN ({format_strings})"
            cursor.execute(query, tuple(user_ids))
            results = cursor.fetchall()
            user_details = {result['id']: result for result in results}
            cache_data = {
                "original_tweet": original_tweet['_source'] if original_tweet else None,
                "retweets": [hit['_source'] for hit in retweet_response['hits']['hits']],
                "user_details": user_details
            }
            cache.put(cache_key, cache_data)  # Cache the results
            print_cached_tweet_details(cache_data)
    finally:
        connection.close()

def print_cached_tweet_details(cached_data):
    original_tweet = cached_data['original_tweet']
    if original_tweet:
        print(f"Original Tweet ID: {original_tweet['id_str']}")
        print(f"Text: {original_tweet['text']}")
        print(f"Likes: {original_tweet['favorite_count']}")
        print(f"Retweets: {original_tweet['retweet_count']}")
        print("Original Tweet User Info:")
        original_user_id = original_tweet['user']['id_str']
        if original_user_id in cached_data['user_details']:
            print_user_info(cached_data['user_details'][original_user_id])
        print("-" * 80)
    
    print("Retweet Details:")
    for retweet in cached_data['retweets']:
        print(f"Retweet ID: {retweet['id_str']}")
        print(f"Text: {retweet['text']}")
        retweet_user_id = retweet['user']['id_str']
        if retweet_user_id in cached_data['user_details']:
            print_user_info(cached_data['user_details'][retweet_user_id])
        print("-" * 80)

def print_user_info(user):
    print(f"User ID: {user['id']}")
    print(f"Name: {user['name']}")
    print(f"Screen Name: {user['screen_name']}")
    print(f"Location: {user['location']}")
    print(f"Verified: {'Yes' if user['verified'] else 'No'}")
    print(f"Followers Count: {user['followers_count']}")
    print(f"Statuses Count: {user['statuses_count']}")
    print(f"Friends Count: {user['friends_count']}")
    print("-" * 40)




# Example usage
start_time = time.time()
find_retweeters_and_print_details("1249403835468009472")
end_time = time.time()
print(f"Total runtime of the program is {end_time - start_time} seconds")



Using cached results for tweet ID: 1249403835468009472
Original Tweet ID: 1249358229265498118
Text: सर आपकी इस हौसला अफजाई से PSUs में निश्चित रूप से नई ऊर्जा का संचार होगा l @dpradhanbjp @BSNLCorporate @OfficeOfRSP… https://t.co/Hig4taqmMZ
Likes: 12
Retweets: 12
Original Tweet User Info:
User ID: 841961917807767553
Name: Adarsh Saxena
Screen Name: AdarshSaxena74
Location: Jaipur, India
Verified: No
Followers Count: 331
Statuses Count: 1235
Friends Count: 246
----------------------------------------
--------------------------------------------------------------------------------
Retweet Details:
Retweet ID: 1249403827234541568
Text: RT @AdarshSaxena74: सर आपकी इस हौसला अफजाई से PSUs में निश्चित रूप से नई ऊर्जा का संचार होगा l @dpradhanbjp @BSNLCorporate @OfficeOfRSP @Ze…
User ID: 101007632
Name: Ravin Gupta
Screen Name: IamRaavin
Location: india
Verified: No
Followers Count: 499
Statuses Count: 4038
Friends Count: 537
----------------------------------------
---------------------------

In [27]:
cache.print_all_keys()

user_29942414
user_716432228
user_365770009
user_1241112951991517188
top_10_tweets
search_Football
search_corona


# Simple GUI

In [11]:
import tkinter as tk
from tkinter import ttk, scrolledtext
from elasticsearch import Elasticsearch
import pymysql
def search_tweets(query_string):
    if not query_string.strip():
        return ["No query provided."]
    query = {
        "query": {
            "function_score": {
                "query": {
                    "bool": {
                        "must": {
                            "match": {
                                "text": query_string
                            }
                        },
                        "filter": {
                            "term": {
                                "isretweet": False
                            }
                        }
                    }
                },
                "functions": [
                    {
                        "field_value_factor": {
                            "field": "engagement_score2",
                            "factor": 1.2,
                            "modifier": "sqrt",
                            "missing": 1
                        }
                    }
                ],
                "boost_mode": "sum"
            }
        },
        "_source": ["created_at", "user.name", "text", "id_str", "retweet_count", "favorite_count", "engagement_score2"],
        "size": 10
    }
    results = es.search(index=index_name, body=query)
    return [f"Tweet ID: {hit['_source']['id_str']}\nUsername: {hit['_source']['user']['name']}\nCreated At: {hit['_source']['created_at']}\nText: {hit['_source']['text']}\nRetweets: {hit['_source']['retweet_count']}\nLikes: {hit['_source']['favorite_count']}\nEngagement Score2: {hit['_source']['engagement_score2']}\n{'-'*40}" for hit in results['hits']['hits']]

def search_user_string(search_string):
    if not search_string.strip():
        return ["No user string provided."]
    query_body = {
        "query": {
            "bool": {
                "must_not": [
                    {"exists": {"field": "retweeted_status"}}
                ],
                "should": [
                    {"match_phrase_prefix": {"user.name": {"query": search_string, "max_expansions": 50}}},
                    {"wildcard": {"user.screen_name": f"*{search_string}*"}}
                ],
                "minimum_should_match": 1
            }
        },
        "_source": ["user.id_str"],
        "size": 1000
    }
    response = es.search(index=index_name, body=query_body)
    user_ids = [hit['_source']['user']['id_str'] for hit in response['hits']['hits']]
    if not user_ids:
        return ["No user found with the given information."]
    
    user_info_results = []
    try:
        with connection.cursor() as cursor:
            format_strings = ','.join(['%s'] * len(user_ids))
            cursor.execute(f"SELECT id, name, screen_name, location, verified, followers_count, statuses_count, friends_count FROM Users4 WHERE id IN ({format_strings})", tuple(user_ids))
            results = cursor.fetchall()
            user_info_results = [f"ID: {user['id']}\nName: {user['name']}\nScreen Name: {user['screen_name']}\nLocation: {user['location']}\nVerified: {'Yes' if user['verified'] else 'No'}\nFollowers Count: {user['followers_count']}\nStatuses Count: {user['statuses_count']}\nFriends Count: {user['friends_count']}\n{'-'*40}" for user in results]
    finally:
        connection.close()
    return user_info_results



def find_retweeters_and_print_details(tweet_id):
    if not tweet_id.strip():
        return ["No tweet ID provided."]
    retweet_query = {
        "query": {
            "term": {"retweeted_status.id_str": tweet_id}
        },
        "_source": ["id_str", "text", "user.id_str", "favorite_count", "retweet_count"],
        "size": 1000
    }
    retweet_response = es.search(index=index_name, body=retweet_query)
    if not retweet_response['hits']['hits']:
        return ["No retweets found for this tweet ID."]
    
    retweet_details = [f"Retweet ID: {hit['_source']['id_str']}\nText: {hit['_source']['text']}\nRetweeter ID: {hit['_source']['user']['id_str']}\nLikes: {hit['_source']['favorite_count']}\nRetweets: {hit['_source']['retweet_count']}\n{'-'*40}" for hit in retweet_response['hits']['hits']]
    return retweet_details

def top_10_tweets():
    query = {
        "size": 10,
        "query": {
            "bool": {
                "must": [
                    {"match": {"isretweet": False}}
                ]
            }
        },
        "sort": [
            {"engagement_score2": {"order": "desc"}}
        ]
    }
    results = es.search(index=index_name, body=query)
    return [f"Tweet: {hit['_source']['text']}\nLikes: {hit['_source']['favorite_count']}\n{'-'*40}" for hit in results['hits']['hits']]

def search_user_tweets(user_id):
    if not user_id.strip():
        return ["No user ID provided."]
    query = {
        "query": {
            "bool": {
                "must": [
                    {"term": {"user.id_str": user_id}}
                ]
            }
        },
        "sort": [{"created_at": {"order": "asc"}}],
        "_source": ["created_at", "text", "isretweet", "retweet_count", "favorite_count"],
        "size": 1000
    }
    results = es.search(index=index_name, body=query)
    return [f"Tweet ID: {hit['_id']}\nText: {hit['_source']['text']}\nRetweets: {hit['_source']['retweet_count']}\nLikes: {hit['_source']['favorite_count']}\nIs Retweet: {'Yes' if hit['_source']['isretweet'] else 'No'}\n{'-'*40}" for hit in results['hits']['hits']]

def execute_search():
    selected_function = function_var.get()
    query = query_entry.get()
    result_text.delete('1.0', tk.END)  # Clear previous results
    if selected_function == 'Search Tweets by String or Hashtag':
        results = search_tweets(query)
    elif selected_function == 'Search User by String':
        results = search_user_string(query)
    elif selected_function == 'Find Retweeters and Details':
        results = find_retweeters_and_print_details(query)
    elif selected_function == 'Top 10 Tweets':
        results = top_10_tweets()
    elif selected_function == 'Search User Tweets and Retweets':
        results = search_user_tweets(query)
    for result in results:
        result_text.insert(tk.END, f"{result}\n")

# GUI Setup
root = tk.Tk()
root.title("Search Interface")

# Dropdown to select the search type
function_var = tk.StringVar()
function_choices = ['Search Tweets by String or Hashtag', 'Search User by String', 'Find Retweeters and Details', 'Top 10 Tweets', 'Search User Tweets and Retweets']
function_var.set(function_choices[0])  # default value
function_menu = ttk.Combobox(root, textvariable=function_var, values=function_choices)
function_menu.pack(pady=10)

# Entry field for query input
query_entry = tk.Entry(root, width=50)
query_entry.pack(pady=10)

# Button to execute search
search_button = tk.Button(root, text="Search", command=execute_search)
search_button.pack(pady=10)

# Text area to display results
result_text = scrolledtext.ScrolledText(root, width=80, height=20)
result_text.pack(pady=10)

root.mainloop()

# Test OR Junk

# Top 10 Tweets (Computing each score at one at a time)

In [267]:
from elasticsearch import Elasticsearch
import pymysql.cursors



# Establish connection to MySQL using pymysql
connection = pymysql.connect(host='localhost',
                             user='root',
                             password='layakishore',
                             database='USERS_DATA',
                             cursorclass=pymysql.cursors.DictCursor)

def fetch_user_details(user_id):
    with connection.cursor() as cursor:
        query = "SELECT name, screen_name, location, followers_count FROM users4 WHERE id = %s"
        cursor.execute(query, (user_id,))
        user_info = cursor.fetchone()
    return user_info

def custom_sort_tweets():
    query = {
        "size": 10,
        "query": {
            "bool": {
                "must": [
                    {"match": {"isretweet": False}}
                ],
                "must_not": [
                    {"exists": {"field": "retweeted_status"}}
                ]
            }
        },
        "sort": {
            "_script": {
                "type": "number",
                "script": {
                    "lang": "painless",
                    "source": "Math.pow(doc['retweet_count'].value, 2) + doc['favorite_count'].value"
                },
                "order": "desc"
            }
        }
    }
    results = es.search(index=index_name, body=query)
    print("Search Results:\n" + "-"*40)  # Print a header and a separator
    for result in results['hits']['hits']:
        tweet = result['_source']
        user_info = fetch_user_details(tweet['user']['id_str'])
        print(f"Tweet ID: {result['_id']}")
        print(f"Text: {tweet.get('text', 'No text available')}")
        print(f"Retweets: {tweet.get('retweet_count', 0)}")
        print(f"Likes: {tweet.get('favorite_count', 0)}")
        print("User Info:")
        if user_info:
            print(f"Name: {user_info['name']}")
            print(f"Screen Name: {user_info['screen_name']}")
            print(f"Location: {user_info['location']}")
            print(f"Followers: {user_info['followers_count']}")
        else:
            print("User details not found.")
        print("-" * 40)

# Run the function

start_time = time.time()
custom_sort_tweets()
end_time = time.time()
print(f"Total runtime of the program is {end_time - start_time} seconds")
# Close the database connection
connection.close()


Search Results:
----------------------------------------
Tweet ID: 1238507133110554625
Text: Everyone criticizing the US response to the corona crisis or our healthcare should really take the time to consider listening to @SenSanders
Retweets: 14235
Likes: 109392
User Info:
Name: Cole M. Sprouse
Screen Name: colesprouse
Location: Tubbytronic Superdome
Followers: 9914883
----------------------------------------
Tweet ID: 1235411751950221312
Text: In this clip, Trump:
1. Denies WHO's coronavirus death rate based on “hunch"
2. Calls coronavirus "corona flu"
3. S… https://t.co/mkSwCySBr0
Retweets: 13482
Likes: 25064
User Info:
Name: Aaron Rupar
Screen Name: atrupar
Location: None
Followers: 303195
----------------------------------------
Tweet ID: 1249041637172482051
Text: Unsung heroes amid Corona pandemic.

Appreciate farmworkers on the field. Appreciate the GRUELING LABOR it takes so… https://t.co/3sytvaOgR6
Retweets: 9456
Likes: 29627
User Info:
Name: StanceGrounded
Screen Name: _SJPea

approach,

1st take all the uniques user ids
for each user id find out all the original tweets
aggregate all the engagement_score2 for all the original tweets made by the user id
now add followers count for userid to this agg engament_score2
do it for all user and sort based on above

print all the user info from mysql for top 10 users



In [37]:
# Establishing connections
connection = pymysql.connect(host='localhost',
                             user='root',
                             password='layakishore',
                             database='USERS_DATA',
                             charset='utf8mb4',
                             cursorclass=pymysql.cursors.DictCursor)


def get_unique_user_ids():
    """ Fetch unique user IDs from the MySQL database """
    with connection.cursor() as cursor:
        cursor.execute("SELECT id FROM users4")
        user_ids = [row['id'] for row in cursor.fetchall()]
        return user_ids

def aggregate_engagement(user_id):
    """ For a given user ID, find all original tweets and sum up engagement_score2 """
    query = {
        
        "query": {
            "bool": {
                "must": [
                    {"term": {"user.id_str": user_id}},
                    {"term": {"isretweet": False}}
                ]
            }
        },
        "aggs": {
            "total_engagement": {
                "sum": {
                    "field": "engagement_score2"
                }
            }
        }
    }
    result = es.search(index=index_name, body=query)
    return result['aggregations']['total_engagement']['value']

def fetch_and_sort_users(user_ids):
    """ Fetch followers count from MySQL and calculate total score """
    user_scores = []
    with connection.cursor() as cursor:
        for user_id in user_ids:
            engagement_score = aggregate_engagement(user_id)
            cursor.execute("SELECT id, name, screen_name, followers_count FROM users4 WHERE id = %s", (user_id,))
            user = cursor.fetchone()
            if user:
              #  print(engagement_score)
                total_score = engagement_score + user['followers_count']
                user['total_score'] = total_score
                user_scores.append(user)
    # Sorting users by total score
    return sorted(user_scores, key=lambda x: x['total_score'], reverse=True)[:10]

def Top_10_users():
    user_ids = get_unique_user_ids()
    if user_ids:
        top_users = fetch_and_sort_users(user_ids)
        for user in top_users:
            print("User ID:", user['id'])
            print("Name:", user['name'])
            print("Screen Name:", user['screen_name'])
            print("Followers Count:", user['followers_count'])
            print("Total Score:", user['total_score'])
            print("-" * 40)


start_time = time.time()
Top_10_users()
end_time = time.time()
print(f"Total runtime of the program is {end_time - start_time} seconds")
# Closing the database connection
connection.close()

User ID: 2863558530
Name: Pre K ❄️
Screen Name: stayfrea_
Followers Count: 69322
Total Score: 89126135268.0
----------------------------------------
User ID: 1100261477989126145
Name: gilbert🚀
Screen Name: HtownBabyG
Followers Count: 672
Total Score: 56315423983.0
----------------------------------------
User ID: 1112592502727548928
Name: D i l l 🦦
Screen Name: Khydill
Followers Count: 3862
Total Score: 32973517323.0
----------------------------------------
User ID: 1131227186
Name: Carlitos 🦉♛
Screen Name: _AyeeCarlos_
Followers Count: 1333
Total Score: 32054764569.0
----------------------------------------
User ID: 728371324184301568
Name: nini🤩
Screen Name: nichellexnicole
Followers Count: 1307
Total Score: 17425216001.0
----------------------------------------
User ID: 813286
Name: Barack Obama
Screen Name: BarackObama
Followers Count: 115603427
Total Score: 16147096941.0
----------------------------------------
User ID: 29942414
Name: ᴹᴿ.ᴰᴿᴱ 💎☣️
Screen Name: MrDre_
Followers Count

# Top 10 Users(Using Cache)

In [19]:
connection = pymysql.connect(host='localhost',
                             user='root',
                             password='layakishore',
                             database='USERS_DATA',
                             charset='utf8mb4',
                             cursorclass=pymysql.cursors.DictCursor)

def get_unique_user_ids():
    """ Fetch unique user IDs from the MySQL database """
    with connection.cursor() as cursor:
        cursor.execute("SELECT id FROM users4")
        user_ids = [row['id'] for row in cursor.fetchall()]
        return user_ids

def aggregate_engagement(user_id):
    """ For a given user ID, find all original tweets and sum up engagement_score2 """
    query = {
        
        "query": {
            "bool": {
                "must": [
                    {"term": {"user.id_str": user_id}},
                    {"term": {"isretweet": False}}
                ]
            }
        },
        "aggs": {
            "total_engagement": {
                "sum": {
                    "field": "engagement_score2"
                }
            }
        }
    }
    result = es.search(index=index_name, body=query)
    return result['aggregations']['total_engagement']['value']

def fetch_and_sort_users(user_ids):
    """ Fetch followers count from MySQL and calculate total score """
    user_scores = []
    with connection.cursor() as cursor:
        for user_id in user_ids:
            engagement_score = aggregate_engagement(user_id)
            cursor.execute("SELECT id, name, screen_name, followers_count FROM users4 WHERE id = %s", (user_id,))
            user = cursor.fetchone()
            if user:
              #  print(engagement_score)
                total_score = engagement_score + user['followers_count']
                user['total_score'] = total_score
                user_scores.append(user)
    # Sorting users by total score
    return sorted(user_scores, key=lambda x: x['total_score'], reverse=True)[:10]
def Top_10_users():
    
    cache_key = "top_10_users"
    top_users = cache.get(cache_key)
    if top_users:
        print("Retrieved top users from cache.")
        for user in top_users:
            print_user_info(user)
        return
    
    user_ids = get_unique_user_ids()
    if user_ids:
        top_users = fetch_and_sort_users(user_ids)
        cache.put(cache_key, top_users)  # Cache the results
        
        for user in top_users:
            print_user_info(user)
    else:
        print("No user IDs available to process.")

def print_user_info(user):
    print("User ID:", user['id'])
    print("Name:", user['name'])
    print("Screen Name:", user['screen_name'])
    print("Followers Count:", user['followers_count'])
    print("Total Score:", user['total_score'])
    print("-" * 40)

start_time = time.time()
Top_10_users()
end_time = time.time()
print(f"Total runtime of the program is {end_time - start_time} seconds")
# Save cache state before closing the application



KeyboardInterrupt: 